In [8]:
import h5py,glob,os
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from pycbc.inference import io, models
from pycbc.workflow import WorkflowConfigParser
from pycbc import conversions
from pycbc import detector
# PLOTTING OPTIONS
fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

params = { 'axes.labelsize': 24,
          'font.family': 'serif',
          'font.serif': 'Computer Modern Raman',
          'font.size': 24,
          'legend.fontsize': 20,
          'xtick.labelsize': 24,
          'ytick.labelsize': 24,
          'axes.grid' : True,
          'text.usetex': True,
          'savefig.dpi' : 100,
          'lines.markersize' : 14,
          'figure.figsize': fig_size}

mpl.rcParams.update(params)

In [15]:
events = ['GW190706_222641','GW191109_010717',
         'GW200129_065458','GW200224_222234']

In [16]:
config_dict = {}
posterior_dict = {}
for e in events:
    print(e)
    config = glob.glob('/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/*'+e+'*.ini')
    config_dict[e]=config[0]
    post = glob.glob('/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/*'+e+'*.hdf')
    posterior_dict[e] = post[0]

GW190706_222641
GW191109_010717
GW200129_065458
GW200224_222234


In [17]:
peak_times = {}
tcs = {}
for event in events:
    if event in posterior_dict:
        print(event)
        cp = WorkflowConfigParser([config_dict[event]])
        fp = io.loadfile(posterior_dict[event], 'r')
        data = fp.read_data()
        psds = fp.read_psds()
        samples = fp.read_samples(fp['samples'].keys())
        fp.close()

        idx = samples['loglikelihood'].argmax()
        maxl_params = {p: samples[p][idx] for p in samples.fieldnames}

        model = models.read_from_config(cp,data=data,psds=psds)

        maxl_params['tc'] = model.static_params['trigger_time'] + maxl_params['delta_tc']
        maxl_params['mass1'] = (1.+maxl_params['redshift']) * maxl_params['srcmass1']
        maxl_params['mass2'] = (1.+maxl_params['redshift']) * maxl_params['srcmass2']
        model.update(**maxl_params)

        _ = model._loglr
        
        signal = model.waveform_generator.generate(**maxl_params)
        td_signal_sum = {}
        for det in model.detectors:
            td_signal_sum[det] = signal[det][0].to_timeseries()**2 \
                               + signal[det][1].to_timeseries()**2
        det = model.detectors[0]
        peak_time = td_signal_sum[det].sample_times[td_signal_sum[det].max_loc()[1]]
        Det = detector.Detector(det)
        delay = Det.time_delay_from_earth_center(maxl_params['ra'],
                                         maxl_params['dec'],
                                         maxl_params['tc'])

        tcs[event] = model.current_params['tc']
        peak_times[event] = peak_time - delay

GW190706_222641


GW191109_010717


GW200129_065458


GW200224_222234


In [18]:
peak_times

{'GW190706_222641': 1246487219.325142,
 'GW191109_010717': 1257296855.1899078,
 'GW200129_065458': 1264316116.4102783,
 'GW200224_222234': 1266618172.369497}

In [19]:
tcs

{'GW190706_222641': 1246487219.3381429,
 'GW191109_010717': 1257296855.1933393,
 'GW200129_065458': 1264316116.4105208,
 'GW200224_222234': 1266618172.381057}